# ✅ 서울 편의점 위치와 매출의 관계 분석

In [1]:
import pandas as pd
import numpy as np
from scipy import stats
import json
import warnings
warnings.filterwarnings('ignore')

print("=" * 80)
print("서울 편의점 위치와 매출의 관계 분석")
print("=" * 80)


서울 편의점 위치와 매출의 관계 분석


In [2]:
# =============================================================================
# 1. 데이터 로드
# =============================================================================
print("\n[1] 데이터 로드 중...")

sales = pd.read_csv('sales_convenience.csv', encoding='utf-8-sig')
population = pd.read_csv('population.csv', encoding='utf-8-sig')
stores = pd.read_csv('store_list.csv', encoding='utf-8-sig')

print(f"  - 매출 데이터: {sales.shape}")
print(f"  - 유동인구 데이터: {population.shape}")
print(f"  - 점포 리스트 데이터: {stores.shape}")



[1] 데이터 로드 중...
  - 매출 데이터: (6097, 53)
  - 유동인구 데이터: (11475, 25)
  - 점포 리스트 데이터: (9597, 10)


In [3]:
# =============================================================================
# 2. 데이터 전처리
# =============================================================================
print("\n[2] 데이터 전처리 중...")

# 2-1. 편의점 밀집도 계산 (행정동별 분기별 편의점 점포 수)
stores['행정동코드'] = stores['행정동코드'].astype(str)
store_density = stores.groupby('행정동코드').size().reset_index(name='점포수')
store_density['행정동코드'] = store_density['행정동코드'].astype(int)
print(f"  - 편의점 밀집도 (행정동 수): {len(store_density)}")

# 2-2. 유동인구 데이터 집계
population_agg = population.groupby(['기준_년분기_코드', '행정동_코드']).agg({
    '총_유동인구_수': 'sum',
    '연령대_10_유동인구_수': 'sum',
    '연령대_20_유동인구_수': 'sum',
    '연령대_30_유동인구_수': 'sum',
    '연령대_40_유동인구_수': 'sum',
    '연령대_50_유동인구_수': 'sum',
    '연령대_60_이상_유동인구_수': 'sum',
    '행정동_코드_명': 'first'
}).reset_index()

# 2-3. 매출 데이터 집계
sales_agg = sales.groupby(['기준_년분기_코드', '행정동_코드']).agg({
    '당월_매출_금액': 'sum',
    '당월_매출_건수': 'sum',
    '연령대_10_매출_금액': 'sum',
    '연령대_20_매출_금액': 'sum',
    '연령대_30_매출_금액': 'sum',
    '연령대_40_매출_금액': 'sum',
    '연령대_50_매출_금액': 'sum',
    '연령대_60_이상_매출_금액': 'sum',
    '행정동_코드_명': 'first'
}).reset_index()

# 2-4. 데이터 병합
df_merged = pd.merge(
    sales_agg, 
    population_agg, 
    on=['기준_년분기_코드', '행정동_코드'],
    how='inner',
    suffixes=('_매출', '_인구')
)

df_merged = pd.merge(
    df_merged,
    store_density,
    left_on='행정동_코드',
    right_on='행정동코드',
    how='left'
)

df_merged['점포수'] = df_merged['점포수'].fillna(0)
print(f"  - 병합된 데이터: {df_merged.shape}")

# 2-5. 분석용 변수 생성
df_merged['유동인구_만명'] = df_merged['총_유동인구_수'] / 10000
df_merged['매출_억원'] = df_merged['당월_매출_금액'] / 100000000

# 점포수가 0인 경우 제외
df_merged_valid = df_merged[df_merged['점포수'] > 0].copy()
df_merged_valid['점포당_매출'] = df_merged_valid['당월_매출_금액'] / df_merged_valid['점포수']

# 연령대별 유동인구 비율
total_pop = df_merged_valid['총_유동인구_수']
df_merged_valid['비율_10대'] = df_merged_valid['연령대_10_유동인구_수'] / total_pop * 100
df_merged_valid['비율_20대'] = df_merged_valid['연령대_20_유동인구_수'] / total_pop * 100
df_merged_valid['비율_30대'] = df_merged_valid['연령대_30_유동인구_수'] / total_pop * 100
df_merged_valid['비율_40대'] = df_merged_valid['연령대_40_유동인구_수'] / total_pop * 100
df_merged_valid['비율_50대'] = df_merged_valid['연령대_50_유동인구_수'] / total_pop * 100
df_merged_valid['비율_60대이상'] = df_merged_valid['연령대_60_이상_유동인구_수'] / total_pop * 100

df_analysis = df_merged_valid.dropna()
print(f"  - 분석용 데이터 (결측치 제거 후): {df_analysis.shape}")



[2] 데이터 전처리 중...
  - 편의점 밀집도 (행정동 수): 428
  - 병합된 데이터: (6097, 21)
  - 분석용 데이터 (결측치 제거 후): (6067, 30)


In [4]:
# =============================================================================
# 3. 탐색적 데이터 분석 (EDA)
# =============================================================================
print("\n" + "=" * 80)
print("[3] 탐색적 데이터 분석 (EDA)")
print("=" * 80)

print("\n[3-1] 주요 변수 기초 통계량")
print("-" * 60)
print(f"\n당월 매출 금액:")
print(f"  평균: {df_analysis['당월_매출_금액'].mean()/1e8:.2f}억원")
print(f"  표준편차: {df_analysis['당월_매출_금액'].std()/1e8:.2f}억원")
print(f"  최소: {df_analysis['당월_매출_금액'].min()/1e8:.2f}억원")
print(f"  최대: {df_analysis['당월_매출_금액'].max()/1e8:.2f}억원")

print(f"\n총 유동인구:")
print(f"  평균: {df_analysis['총_유동인구_수'].mean()/1e4:.2f}만명")
print(f"  표준편차: {df_analysis['총_유동인구_수'].std()/1e4:.2f}만명")

print(f"\n점포수 (밀집도):")
print(f"  평균: {df_analysis['점포수'].mean():.1f}개")
print(f"  표준편차: {df_analysis['점포수'].std():.1f}개")
print(f"  최소: {df_analysis['점포수'].min():.0f}개")
print(f"  최대: {df_analysis['점포수'].max():.0f}개")



[3] 탐색적 데이터 분석 (EDA)

[3-1] 주요 변수 기초 통계량
------------------------------------------------------------

당월 매출 금액:
  평균: 27.19억원
  표준편차: 32.07억원
  최소: 0.00억원
  최대: 351.91억원

총 유동인구:
  평균: 563.53만명
  표준편차: 296.58만명

점포수 (밀집도):
  평균: 23.2개
  표준편차: 17.3개
  최소: 1개
  최대: 157개


In [5]:
# =============================================================================
# 4. 정규성 검정
# =============================================================================
print("\n" + "=" * 80)
print("[4] 정규성 검정 (Shapiro-Wilk Test)")
print("=" * 80)

sample_size = min(len(df_analysis), 5000)
sample_df = df_analysis.sample(n=sample_size, random_state=42)

print(f"\n표본 크기: {sample_size}")
print("-" * 60)

normality_results = {}
for var, label in [('당월_매출_금액', '매출'), ('총_유동인구_수', '유동인구'), ('점포수', '점포수')]:
    stat, p_value = stats.shapiro(sample_df[var])
    normality = "정규분포 따름" if p_value > 0.05 else "정규분포 따르지 않음"
    normality_results[label] = {'stat': stat, 'p_value': p_value, 'normal': p_value > 0.05}
    print(f"{label}:")
    print(f"  통계량: {stat:.4f}, p-value: {p_value:.6f}")
    print(f"  결론: {normality}")
    print()



[4] 정규성 검정 (Shapiro-Wilk Test)

표본 크기: 5000
------------------------------------------------------------
매출:
  통계량: 0.6403, p-value: 0.000000
  결론: 정규분포 따르지 않음

유동인구:
  통계량: 0.9141, p-value: 0.000000
  결론: 정규분포 따르지 않음

점포수:
  통계량: 0.7356, p-value: 0.000000
  결론: 정규분포 따르지 않음



In [6]:
# =============================================================================
# 5. 상관분석
# =============================================================================
print("\n" + "=" * 80)
print("[5] 상관분석")
print("=" * 80)

target = df_analysis['당월_매출_금액']
correlation_results = {}

print("\n[5-1] 매출과 주요 변수 간 상관관계")
print("-" * 60)
print(f"{'변수':<20} {'상관계수':>10} {'p-value':>12} {'유의성':>10}")
print("-" * 60)

for var, label in [('총_유동인구_수', '유동인구'), ('점포수', '밀집도(점포수)'), 
                   ('비율_20대', '20대 비율'), ('비율_30대', '30대 비율'),
                   ('비율_40대', '40대 비율'), ('비율_50대', '50대 비율'),
                   ('비율_60대이상', '60대이상 비율')]:
    r, p = stats.pearsonr(target, df_analysis[var])
    sig = "***" if p < 0.001 else "**" if p < 0.01 else "*" if p < 0.05 else "N.S."
    correlation_results[label] = {'r': r, 'p_value': p}
    print(f"{label:<20} {r:>10.4f} {p:>12.6f} {sig:>10}")



[5] 상관분석

[5-1] 매출과 주요 변수 간 상관관계
------------------------------------------------------------
변수                         상관계수      p-value        유의성
------------------------------------------------------------
유동인구                     0.4985     0.000000        ***
밀집도(점포수)                 0.8728     0.000000        ***
20대 비율                   0.3510     0.000000        ***
30대 비율                   0.4517     0.000000        ***
40대 비율                   0.2338     0.000000        ***
50대 비율                  -0.2698     0.000000        ***
60대이상 비율                -0.4593     0.000000        ***


In [7]:
# =============================================================================
# 6. 다중 회귀분석 (수동 구현)
# =============================================================================
print("\n" + "=" * 80)
print("[6] 다중 회귀분석")
print("=" * 80)

def multiple_regression(X, y):
    """OLS 회귀분석 수동 구현"""
    n = len(y)
    k = X.shape[1]  # 변수 수 (상수항 포함)
    
    # 회귀계수 계산: β = (X'X)^(-1)X'y
    XtX = X.T @ X
    XtX_inv = np.linalg.inv(XtX)
    Xty = X.T @ y
    beta = XtX_inv @ Xty
    
    # 예측값 및 잔차
    y_pred = X @ beta
    residuals = y - y_pred
    
    # SST, SSE, SSR
    y_mean = y.mean()
    SST = np.sum((y - y_mean) ** 2)
    SSE = np.sum(residuals ** 2)
    SSR = SST - SSE
    
    # R-squared
    R2 = 1 - (SSE / SST)
    adj_R2 = 1 - (1 - R2) * (n - 1) / (n - k)
    
    # MSE, 표준오차
    MSE = SSE / (n - k)
    se_beta = np.sqrt(np.diag(MSE * XtX_inv))
    
    # t-통계량 및 p-value
    t_stats = beta / se_beta
    p_values = 2 * (1 - stats.t.cdf(np.abs(t_stats), n - k))
    
    # F-통계량
    MSR = SSR / (k - 1)
    F_stat = MSR / MSE
    F_pvalue = 1 - stats.f.cdf(F_stat, k - 1, n - k)
    
    return {
        'beta': beta,
        'se': se_beta,
        't_stats': t_stats,
        'p_values': p_values,
        'R2': R2,
        'adj_R2': adj_R2,
        'F_stat': F_stat,
        'F_pvalue': F_pvalue,
        'residuals': residuals,
        'fitted': y_pred,
        'SSE': SSE,
        'n': n,
        'k': k
    }

# 6-1. 기본 모델: 유동인구 + 점포수
print("\n[6-1] 기본 모델 (유동인구 + 점포 밀집도)")
print("-" * 60)

y = df_analysis['당월_매출_금액'].values
X_basic = np.column_stack([
    np.ones(len(y)),  # 상수항
    df_analysis['총_유동인구_수'].values,
    df_analysis['점포수'].values
])

result_basic = multiple_regression(X_basic, y)
var_names_basic = ['상수항', '유동인구', '점포수(밀집도)']

print(f"\n{'변수':<20} {'회귀계수':>15} {'표준오차':>12} {'t-통계량':>10} {'p-value':>12}")
print("-" * 70)
for i, name in enumerate(var_names_basic):
    print(f"{name:<20} {result_basic['beta'][i]:>15.4f} {result_basic['se'][i]:>12.4f} {result_basic['t_stats'][i]:>10.2f} {result_basic['p_values'][i]:>12.6f}")

print(f"\nR-squared: {result_basic['R2']:.4f}")
print(f"Adjusted R-squared: {result_basic['adj_R2']:.4f}")
print(f"F-statistic: {result_basic['F_stat']:.2f} (p-value: {result_basic['F_pvalue']:.6f})")

# 6-2. 확장 모델: 연령대 비율 포함
print("\n\n[6-2] 확장 모델 (연령대 비율 포함)")
print("-" * 60)

X_extended = np.column_stack([
    np.ones(len(y)),
    df_analysis['총_유동인구_수'].values,
    df_analysis['점포수'].values,
    df_analysis['비율_20대'].values,
    df_analysis['비율_30대'].values,
    df_analysis['비율_40대'].values,
    df_analysis['비율_50대'].values
])

result_extended = multiple_regression(X_extended, y)
var_names_extended = ['상수항', '유동인구', '점포수(밀집도)', '20대비율', '30대비율', '40대비율', '50대비율']

print(f"\n{'변수':<20} {'회귀계수':>15} {'표준오차':>12} {'t-통계량':>10} {'p-value':>12}")
print("-" * 70)
for i, name in enumerate(var_names_extended):
    sig = "***" if result_extended['p_values'][i] < 0.001 else "**" if result_extended['p_values'][i] < 0.01 else "*" if result_extended['p_values'][i] < 0.05 else ""
    print(f"{name:<20} {result_extended['beta'][i]:>15.4f} {result_extended['se'][i]:>12.4f} {result_extended['t_stats'][i]:>10.2f} {result_extended['p_values'][i]:>12.6f} {sig}")

print(f"\nR-squared: {result_extended['R2']:.4f}")
print(f"Adjusted R-squared: {result_extended['adj_R2']:.4f}")
print(f"F-statistic: {result_extended['F_stat']:.2f} (p-value: {result_extended['F_pvalue']:.6f})")



[6] 다중 회귀분석

[6-1] 기본 모델 (유동인구 + 점포 밀집도)
------------------------------------------------------------

변수                              회귀계수         표준오차      t-통계량      p-value
----------------------------------------------------------------------
상수항                  -1119919590.7719 43705913.7884     -25.62     0.000000
유동인구                         19.6017       8.1564       2.40     0.016281
점포수(밀집도)              160397929.1935 1402216.5877     114.39     0.000000

R-squared: 0.7620
Adjusted R-squared: 0.7619
F-statistic: 9708.81 (p-value: 0.000000)


[6-2] 확장 모델 (연령대 비율 포함)
------------------------------------------------------------

변수                              회귀계수         표준오차      t-통계량      p-value
----------------------------------------------------------------------
상수항                  -4735336850.0870 350760731.0284     -13.50     0.000000 ***
유동인구                         36.9242       8.0917       4.56     0.000005 ***
점포수(밀집도)              148780733.1349 1602434.686

In [8]:
# =============================================================================
# 7. 다중공선성 검정 (VIF)
# =============================================================================
print("\n" + "=" * 80)
print("[7] 다중공선성 검정 (VIF)")
print("=" * 80)

def calculate_vif(X):
    """VIF 계산"""
    vif_values = []
    for i in range(X.shape[1]):
        # i번째 변수를 종속변수로, 나머지를 독립변수로 회귀
        y_i = X[:, i]
        X_others = np.delete(X, i, axis=1)
        X_others_const = np.column_stack([np.ones(len(y_i)), X_others])
        
        # R² 계산
        result = multiple_regression(X_others_const, y_i)
        r2_i = result['R2']
        
        # VIF = 1 / (1 - R²)
        vif = 1 / (1 - r2_i) if r2_i < 1 else np.inf
        vif_values.append(vif)
    return vif_values

print("\n[7-1] 기본 모델 VIF")
print("-" * 60)
X_vif_basic = np.column_stack([
    df_analysis['총_유동인구_수'].values,
    df_analysis['점포수'].values
])
vif_basic = calculate_vif(X_vif_basic)

print(f"{'변수':<20} {'VIF':>10} {'해석':>15}")
print("-" * 50)
for name, vif in zip(['유동인구', '점포수(밀집도)'], vif_basic):
    interpretation = "문제없음" if vif < 5 else "주의필요" if vif < 10 else "심각"
    print(f"{name:<20} {vif:>10.2f} {interpretation:>15}")

print("\n[7-2] 확장 모델 VIF")
print("-" * 60)
X_vif_ext = np.column_stack([
    df_analysis['총_유동인구_수'].values,
    df_analysis['점포수'].values,
    df_analysis['비율_20대'].values,
    df_analysis['비율_30대'].values,
    df_analysis['비율_40대'].values,
    df_analysis['비율_50대'].values
])
vif_extended = calculate_vif(X_vif_ext)

print(f"{'변수':<20} {'VIF':>10} {'해석':>15}")
print("-" * 50)
for name, vif in zip(['유동인구', '점포수', '20대비율', '30대비율', '40대비율', '50대비율'], vif_extended):
    interpretation = "문제없음" if vif < 5 else "주의필요" if vif < 10 else "심각"
    print(f"{name:<20} {vif:>10.2f} {interpretation:>15}")



[7] 다중공선성 검정 (VIF)

[7-1] 기본 모델 VIF
------------------------------------------------------------
변수                          VIF              해석
--------------------------------------------------
유동인구                       1.45            문제없음
점포수(밀집도)                   1.45            문제없음

[7-2] 확장 모델 VIF
------------------------------------------------------------
변수                          VIF              해석
--------------------------------------------------
유동인구                       1.50            문제없음
점포수                        1.98            문제없음
20대비율                      3.00            문제없음
30대비율                      1.74            문제없음
40대비율                      2.08            문제없음
50대비율                      1.60            문제없음


In [9]:
# =============================================================================
# 8. 잔차 분석
# =============================================================================
print("\n" + "=" * 80)
print("[8] 잔차 분석")
print("=" * 80)

residuals = result_basic['residuals']
fitted_values = result_basic['fitted']

print("\n[8-1] 잔차 기본 통계")
print("-" * 60)
print(f"  잔차 평균: {residuals.mean():.4f} (0에 가까워야 함)")
print(f"  잔차 표준편차: {residuals.std()/1e8:.2f}억원")
print(f"  잔차 최소: {residuals.min()/1e8:.2f}억원")
print(f"  잔차 최대: {residuals.max()/1e8:.2f}억원")

# 정규성 검정 (잔차)
print("\n[8-2] 잔차 정규성 검정 (Shapiro-Wilk)")
print("-" * 60)
sample_residuals = np.random.choice(residuals, size=min(5000, len(residuals)), replace=False)
stat, p_value = stats.shapiro(sample_residuals)
print(f"  통계량: {stat:.4f}")
print(f"  p-value: {p_value:.6f}")
if p_value > 0.05:
    print("  결론: 잔차가 정규분포를 따른다고 볼 수 있습니다.")
else:
    print("  주의: 잔차가 정규분포를 따르지 않을 수 있습니다.")
    print("        (대규모 데이터에서는 정규성 위배가 흔히 발생합니다)")

# Durbin-Watson 검정 (자기상관)
print("\n[8-3] Durbin-Watson 검정 (자기상관)")
print("-" * 60)
diff_resid = np.diff(residuals)
dw_stat = np.sum(diff_resid ** 2) / np.sum(residuals ** 2)
print(f"  Durbin-Watson 통계량: {dw_stat:.4f}")
if 1.5 < dw_stat < 2.5:
    print("  결론: 자기상관 없음 (1.5 ~ 2.5 범위)")
else:
    print("  주의: 자기상관 가능성 있음")


[8] 잔차 분석

[8-1] 잔차 기본 통계
------------------------------------------------------------
  잔차 평균: -0.0000 (0에 가까워야 함)
  잔차 표준편차: 15.65억원
  잔차 최소: -64.08억원
  잔차 최대: 107.09억원

[8-2] 잔차 정규성 검정 (Shapiro-Wilk)
------------------------------------------------------------
  통계량: 0.9235
  p-value: 0.000000
  주의: 잔차가 정규분포를 따르지 않을 수 있습니다.
        (대규모 데이터에서는 정규성 위배가 흔히 발생합니다)

[8-3] Durbin-Watson 검정 (자기상관)
------------------------------------------------------------
  Durbin-Watson 통계량: 1.8433
  결론: 자기상관 없음 (1.5 ~ 2.5 범위)


In [11]:
# =============================================================================
# 9. 모델 비교 (F-test)
# =============================================================================
print("\n" + "=" * 80)
print("[9] 모델 비교 (연령대 변수 포함 여부)")
print("=" * 80)

# F-test for nested models
SSE_basic = result_basic['SSE']
SSE_extended = result_extended['SSE']
df_basic = result_basic['n'] - result_basic['k']
df_extended = result_extended['n'] - result_extended['k']

f_stat = ((SSE_basic - SSE_extended) / (df_basic - df_extended)) / (SSE_extended / df_extended)
p_value_f = 1 - stats.f.cdf(f_stat, df_basic - df_extended, df_extended)

print(f"\n[9-1] 중첩 모델 F-검정")
print("-" * 60)
print(f"  기본 모델 SSE: {SSE_basic/1e18:.4f}")
print(f"  확장 모델 SSE: {SSE_extended/1e18:.4f}")
print(f"  F-statistic: {f_stat:.4f}")
print(f"  p-value: {p_value_f:.6f}")

if p_value_f < 0.05:
    print("\n  결론: 연령대 변수를 포함한 확장 모델이 통계적으로 유의하게 더 좋습니다.")
    recommend_age = True
else:
    print("\n  결론: 연령대 변수 추가가 모델 개선에 유의한 기여를 하지 않습니다.")
    recommend_age = False



[9] 모델 비교 (연령대 변수 포함 여부)

[9-1] 중첩 모델 F-검정
------------------------------------------------------------
  기본 모델 SSE: 14850.4645
  확장 모델 SSE: 14156.0187
  F-statistic: 74.3207
  p-value: 0.000000

  결론: 연령대 변수를 포함한 확장 모델이 통계적으로 유의하게 더 좋습니다.


In [12]:
# =============================================================================
# 10. 최종 결론
# =============================================================================
print("\n" + "=" * 80)
print("[10] 최종 분석 결론")
print("=" * 80)

print("""
📊 분석 결과 요약:

1. 유동인구와 매출의 관계:""")
r_pop = correlation_results['유동인구']['r']
p_pop = correlation_results['유동인구']['p_value']
print(f"   - 상관계수: {r_pop:.4f} (p-value: {p_pop:.6f})")
if p_pop < 0.05:
    direction = "양의" if r_pop > 0 else "음의"
    strength = "강한" if abs(r_pop) > 0.5 else "중간" if abs(r_pop) > 0.3 else "약한"
    print(f"   - 유동인구와 매출 사이에 통계적으로 유의한 {strength} {direction} 상관관계가 있습니다.")

print("""
2. 편의점 밀집도와 매출의 관계:""")
r_store = correlation_results['밀집도(점포수)']['r']
p_store = correlation_results['밀집도(점포수)']['p_value']
print(f"   - 상관계수: {r_store:.4f} (p-value: {p_store:.6f})")
if p_store < 0.05:
    direction = "양의" if r_store > 0 else "음의"
    strength = "강한" if abs(r_store) > 0.5 else "중간" if abs(r_store) > 0.3 else "약한"
    print(f"   - 점포 밀집도와 매출 사이에 통계적으로 유의한 {strength} {direction} 상관관계가 있습니다.")

print("""
3. 회귀분석 결과:""")
print(f"   - 기본 모델 R²: {result_basic['R2']:.4f} ({result_basic['R2']*100:.1f}%)")
print(f"   - 확장 모델 R²: {result_extended['R2']:.4f} ({result_extended['R2']*100:.1f}%)")
print(f"   - R² 향상: {(result_extended['R2'] - result_basic['R2'])*100:.2f}%p")

print("""
4. 연령대 변수 포함 권장 여부:""")
if recommend_age:
    print("   ✅ 연령대 변수를 포함하는 것을 권장합니다.")
    print("   - F-검정 결과 확장 모델이 통계적으로 유의하게 더 좋습니다.")
    
    # 유의한 연령대 변수 확인
    age_indices = [3, 4, 5, 6]  # 20대, 30대, 40대, 50대
    age_names = ['20대비율', '30대비율', '40대비율', '50대비율']
    print("\n   유의한 연령대 변수:")
    for idx, name in zip(age_indices, age_names):
        if result_extended['p_values'][idx] < 0.05:
            coef = result_extended['beta'][idx]
            direction = "양(+)" if coef > 0 else "음(-)"
            print(f"   - {name}: 회귀계수={coef/1e8:.4f}억원, p={result_extended['p_values'][idx]:.4f} → {direction}의 효과")
else:
    print("   ⚠️ 기본 모델(유동인구 + 밀집도)만으로 충분합니다.")
    print("   - 연령대 변수의 추가적인 설명력 기여가 통계적으로 유의하지 않습니다.")

print("""
5. 다중공선성:""")
max_vif = max(vif_extended)
print(f"   - 최대 VIF: {max_vif:.2f}")
if max_vif < 5:
    print("   - 모든 VIF < 5로 다중공선성 문제 없음")
elif max_vif < 10:
    print("   - 일부 변수 VIF 5~10으로 주의 필요")
else:
    print("   - VIF > 10인 변수 존재, 다중공선성 문제 있음")

print("""
6. 잔차 분석:""")
print(f"   - 잔차 평균: {residuals.mean():.4f} (0에 가까워 적절)")
print(f"   - Durbin-Watson: {dw_stat:.4f}", end="")
if 1.5 < dw_stat < 2.5:
    print(" (자기상관 없음)")
else:
    print(" (자기상관 가능성)")

print("\n" + "=" * 80)
print("분석 완료!")
print("=" * 80)


[10] 최종 분석 결론

📊 분석 결과 요약:

1. 유동인구와 매출의 관계:
   - 상관계수: 0.4985 (p-value: 0.000000)
   - 유동인구와 매출 사이에 통계적으로 유의한 중간 양의 상관관계가 있습니다.

2. 편의점 밀집도와 매출의 관계:
   - 상관계수: 0.8728 (p-value: 0.000000)
   - 점포 밀집도와 매출 사이에 통계적으로 유의한 강한 양의 상관관계가 있습니다.

3. 회귀분석 결과:
   - 기본 모델 R²: 0.7620 (76.2%)
   - 확장 모델 R²: 0.7732 (77.3%)
   - R² 향상: 1.11%p

4. 연령대 변수 포함 권장 여부:
   ✅ 연령대 변수를 포함하는 것을 권장합니다.
   - F-검정 결과 확장 모델이 통계적으로 유의하게 더 좋습니다.

   유의한 연령대 변수:
   - 20대비율: 회귀계수=0.3380억원, p=0.0000 → 양(+)의 효과
   - 30대비율: 회귀계수=0.1801억원, p=0.0107 → 양(+)의 효과
   - 40대비율: 회귀계수=1.7369억원, p=0.0000 → 양(+)의 효과

5. 다중공선성:
   - 최대 VIF: 3.00
   - 모든 VIF < 5로 다중공선성 문제 없음

6. 잔차 분석:
   - 잔차 평균: -0.0000 (0에 가까워 적절)
   - Durbin-Watson: 1.8433 (자기상관 없음)

분석 완료!


In [13]:
import pandas as pd

pop = pd.read_csv("population.csv")
sales = pd.read_csv("sales_convenience.csv")
store = pd.read_csv("store_list.csv")





# ✅ 시각화

## 1️⃣ 서울 편의점 전체 위치 지도

In [14]:
import plotly.express as px

fig = px.scatter_mapbox(
    store,
    lat="위도",
    lon="경도",
    hover_name="상호명",
    hover_data=["행정동명", "시군구명"],
    zoom=10,
    height=600,
    color_discrete_sequence=["rgba(0,0,255,0.5)"]
)

fig.update_layout(
    mapbox_style="open-street-map",
    title="서울시 편의점 전체 위치 분포",
    margin={"r":0,"t":40,"l":0,"b":0}
)

fig.show()


## 2️⃣ 행정동별 매출 지도 (Plotly)

In [15]:
# 행정동별 매출 집계
dong_sales = (
    sales
    .groupby(["행정동_코드", "행정동_코드_명"], as_index=False)
    ["당월_매출_금액"]
    .sum()
)

# 행정동 중심 좌표 만들기
dong_center = (
    store
    .groupby("행정동명")[["위도", "경도"]]
    .mean()
    .reset_index()
    .rename(columns={"행정동명": "행정동_코드_명"})
)

# 병합
dong_map = pd.merge(
    dong_sales,
    dong_center,
    on="행정동_코드_명",
    how="inner"
)

dong_map["당월_매출_금액"] = pd.to_numeric(
    dong_map["당월_매출_금액"],
    errors="coerce"
)

# plotly 지도
fig = px.scatter_mapbox(
    dong_map,
    lat="위도",
    lon="경도",
    size="당월_매출_금액",
    color="당월_매출_금액",
    color_continuous_scale="Viridis", 
    hover_name="행정동_코드_명",
    zoom=10,
    height=600,
    size_max=40
)


fig.update_layout(
    mapbox_style="open-street-map",
    title="행정동별 편의점 매출 분포 (중심점 기준)",
    margin={"r":0,"t":40,"l":0,"b":0}
)

fig.show()


## 3️⃣ 고급 지도: 행정동 매출 + 편의점 위치 겹치기 ⭐

In [32]:
import pandas as pd
import json
import plotly.express as px
import plotly.graph_objects as go

# ===============================
# 1️⃣ GeoJSON 로드
# ===============================
with open("hangjeongdong_서울특별시.geojson", encoding="utf-8") as f:
    seoul_geo = json.load(f)

# ===============================
# 2️⃣ 행정동 매출 집계
# ===============================
sales_dong = (
    sales
    .groupby(["행정동_코드", "행정동_코드_명"], as_index=False)
    ["당월_매출_금액"]
    .sum()
)

# 🔥 핵심: 행정동 코드 문자열 변환, 10자리 맞추기
sales_dong["행정동_코드"] = sales_dong["행정동_코드"].astype(str).str.ljust(10, "0")

# ===============================
# 3️⃣ Choropleth 지도 생성
# ===============================
fig = px.choropleth_mapbox(
    sales_dong,
    geojson=seoul_geo,
    locations="행정동_코드",
    featureidkey="properties.adm_cd2",
    color="당월_매출_금액",
    color_continuous_scale="Viridis",        # 세련된 색상
    hover_name="행정동_코드_명",
    hover_data={"당월_매출_금액": ":,.0f"},
    mapbox_style="carto-positron",
    zoom=10,
    center={"lat": 37.56, "lon": 126.98},
    opacity=0.6,
    height=700
)

# ===============================
# 4️⃣ 지도 스타일
# ===============================
# 경계선
fig.update_traces(
    marker_line_width=0.6,
    marker_line_color="rgba(0,0,0,0.4)"
)

# 행정동 이름 텍스트 표시
fig.add_trace(go.Scattermapbox(
    lat=dong_center["위도"],
    lon=dong_center["경도"],
    mode="text",
    text=dong_center["행정동_코드_명"],
    textfont=dict(size=10, color="rgba(50,50,50,0.85)"),
    name="행정동명",
    hoverinfo="skip"
))

# 컬러바와 레이아웃
fig.update_layout(
    title=dict(
        text="서울시 행정동별 편의점 매출 분포",
        x=0.5,
        font=dict(size=20)
    ),
    coloraxis_colorbar=dict(
        title="당월 매출 (원)",
        ticks="outside",
        tickformat=",.0f"
    ),
    margin={"r":0,"t":60,"l":0,"b":0}
)

# ===============================
# 5️⃣ 지도 출력
# ===============================
fig.show()



In [33]:
missing_dong = seoul_geo['features']
missing_codes = [f['properties']['adm_cd2'] for f in missing_dong if f['properties']['adm_cd2'] not in sales_dong['행정동_코드'].values]
print("매출 데이터 없는 행정동 코드:", missing_codes)


매출 데이터 없는 행정동 코드: ['1111068000', '1120058000', '1138065000', '1141052000', '1141069000', '1153080000', '1154568000', '1162071500', '1165055000', '1168066000', '1171072000']


In [28]:
# geojson에서 모든 행정동 코드와 이름 추출
geo_codes = [f['properties']['adm_cd2'] for f in seoul_geo['features']]
geo_names = [f['properties']['adm_nm'] for f in seoul_geo['features']]

geo_df = pd.DataFrame({"행정동_코드": geo_codes, "행정동_코드_명": geo_names})

# sales_dong에 없는 행정동 찾기
missing_dong = geo_df[~geo_df["행정동_코드"].isin(sales_dong["행정동_코드"])]

print("매출이 없는 행정동:")
print(missing_dong[["행정동_코드", "행정동_코드_명"]])


매출이 없는 행정동:
         행정동_코드          행정동_코드_명
11   1111068000    서울특별시 종로구 창신2동
53   1120058000     서울특별시 성동구 응봉동
187  1138065000     서울특별시 은평구 수색동
192  1141052000    서울특별시 서대문구 천연동
198  1141069000  서울특별시 서대문구 남가좌1동
270  1153080000      서울특별시 구로구 항동
281  1154568000    서울특별시 금천구 시흥2동
330  1162071500     서울특별시 관악구 난향동
344  1165055000    서울특별시 서초구 반포본동
368  1168066000    서울특별시 강남구 개포1동
401  1171072000    서울특별시 송파구 잠실7동


## 4️⃣ Scatter + 회귀선 (유동인구 vs 매출)

In [34]:
import pandas as pd

pop = pd.read_csv("population.csv")
sales = pd.read_csv("sales_convenience.csv")

pop_dong = (
    pop
    .groupby(["행정동_코드", "행정동_코드_명"], as_index=False)
    ["총_유동인구_수"]
    .mean()
)

sales_dong = (
    sales
    .groupby(["행정동_코드", "행정동_코드_명"], as_index=False)
    ["당월_매출_금액"]
    .sum()
)


In [35]:
df = pd.merge(
    pop_dong,
    sales_dong,
    on=["행정동_코드", "행정동_코드_명"],
    how="inner"
)

df.head()


행정동_코드 행정동_코드_명      총_유동인구_수     당월_매출_금액
0  11110515    청운효자동  3.642656e+06  18035680963
1  11110530      사직동  3.969589e+06  67298758498
2  11110540      삼청동  9.355883e+05  13171867648
3  11110550      부암동  1.147292e+06  11253160989
4  11110560      평창동  9.208158e+05   7531545515

In [36]:
import numpy as np
import plotly.graph_objects as go

x = df["총_유동인구_수"]
y = df["당월_매출_금액"]

coef = np.polyfit(x, y, 1)
x_line = np.linspace(x.min(), x.max(), 100)
y_line = coef[0] * x_line + coef[1]

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=x,
    y=y,
    mode="markers",
    opacity=0.5,
    name="행정동"
))

fig.add_trace(go.Scatter(
    x=x_line,
    y=y_line,
    mode="lines",
    line=dict(width=3),
    name="Regression Line"
))

fig.update_layout(
    title="유동인구 vs 편의점 매출 (행정동 단위)",
    xaxis_title="총 유동인구",
    yaxis_title="당월 매출 금액",
    template="plotly_white"
)

fig.show()



## 5️⃣ 연령대 비율 vs 매출 Scatter

In [37]:
# 연령대별 매출 비율
sales["연령대_20_비율"] = sales["연령대_20_매출_금액"] / sales["당월_매출_금액"]
sales["연령대_30_비율"] = sales["연령대_30_매출_금액"] / sales["당월_매출_금액"]
sales["연령대_40_비율"] = sales["연령대_40_매출_금액"] / sales["당월_매출_금액"]
sales["연령대_50_비율"] = sales["연령대_50_매출_금액"] / sales["당월_매출_금액"]
sales["연령대_60_비율"] = sales["연령대_60_이상_매출_금액"] / sales["당월_매출_금액"]



In [38]:
import plotly.graph_objects as go

fig = go.Figure()

age_cols = {
    "20대": "연령대_20_비율",
    "30대": "연령대_30_비율",
    "40대": "연령대_40_비율",
    "50대": "연령대_50_비율",
    "60대 이상": "연령대_60_비율"
}

for age, col in age_cols.items():
    fig.add_trace(go.Scatter(
        x=sales[col],
        y=sales["당월_매출_금액"],
        mode="markers",
        name=age,
        opacity=0.45
    ))

fig.update_layout(
    title="연령대별 매출 비중과 편의점 전체 매출 관계",
    xaxis_title="연령대별 매출 비중",
    yaxis_title="당월 매출 금액",
    template="plotly_white",
    height=600
)

fig.show()


# 시각화

In [39]:
import json
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

# JSON 로드
with open('analysis_results.json', 'r', encoding='utf-8') as f:
    data = json.load(f)


In [40]:
corr_df = pd.DataFrame({
    '변수': data['correlation']['variables'],
    '상관계수(r)': data['correlation']['r_values'],
    'p-value': data['correlation']['p_values']
})

fig_corr = px.bar(
    corr_df,
    x='변수',
    y='상관계수(r)',
    color='p-value',
    color_continuous_scale='RdBu',
    title='변수별 상관계수'
)

fig_corr.show()


In [41]:
coef_basic = pd.DataFrame({
    '변수': data['regression_basic']['coefficients'].keys(),
    '계수': data['regression_basic']['coefficients'].values(),
    '모델': '기본'
})

coef_ext = pd.DataFrame({
    '변수': data['regression_extended']['coefficients'].keys(),
    '계수': data['regression_extended']['coefficients'].values(),
    '모델': '확장'
})

coef_df = pd.concat([coef_basic, coef_ext])

fig_coef = px.bar(
    coef_df,
    x='변수',
    y='계수',
    color='모델',
    barmode='group',
    title='회귀계수 비교 (기본 vs 확장 모델)'
)

fig_coef.show()


In [42]:
vif_basic_df = pd.DataFrame({
    '변수': data['vif']['basic'].keys(),
    'VIF': data['vif']['basic'].values(),
    '모델': '기본'
})

vif_ext_df = pd.DataFrame({
    '변수': data['vif']['extended'].keys(),
    'VIF': data['vif']['extended'].values(),
    '모델': '확장'
})

vif_df = pd.concat([vif_basic_df, vif_ext_df])

fig_vif = px.bar(
    vif_df,
    x='변수',
    y='VIF',
    color='모델',
    barmode='group',
    title='VIF 비교'
)

fig_vif.add_hline(y=10, line_dash='dash', line_color='red',
                  annotation_text='VIF=10 기준')

fig_vif.show()

In [43]:
res = data['residual_analysis']

fig_res = go.Figure()

metrics = {
    '잔차 평균': res['mean'],
    '잔차 표준편차': res['std'],
    'Durbin-Watson': res['durbin_watson'],
    '정규성 p-value': res['normality_p']
}

for i, (k, v) in enumerate(metrics.items()):
    fig_res.add_trace(go.Indicator(
        mode='number',
        value=v,
        title={'text': k},
        domain={'row': 0, 'column': i}
    ))

fig_res.update_layout(
    grid={'rows': 1, 'columns': 4},
    title='잔차 분석 요약'
)

fig_res.show()


In [44]:
scatter_df = pd.DataFrame({
    '유동인구': data['scatter_data']['population'],
    '매출': data['scatter_data']['sales'],
    '점포수': data['scatter_data']['store_count'],
    '행정동': data['scatter_data']['district']
})

fig_scatter = px.scatter(
    scatter_df,
    x='유동인구',
    y='매출',
    size='점포수',
    color='행정동',
    color_continuous_scale="Viridis",
    hover_data=['점포수'],
    title='유동인구와 매출의 관계'
)

fig_scatter.show()

In [45]:
import json
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import scipy.stats as stats

with open('analysis_results.json', 'r', encoding='utf-8') as f:
    data = json.load(f)


In [46]:
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=(
        '상관계수',
        '회귀계수 비교',
        'VIF',
        '유동인구 vs 매출'
    )
)

# ① 상관계수
fig.add_trace(
    go.Bar(
        x=data['correlation']['variables'],
        y=data['correlation']['r_values'],
        name='Correlation'
    ),
    row=1, col=1
)

# ② 회귀계수
for model, reg in [('기본', 'regression_basic'), ('확장', 'regression_extended')]:
    fig.add_trace(
        go.Bar(
            x=list(data[reg]['coefficients'].keys()),
            y=list(data[reg]['coefficients'].values()),
            name=model
        ),
        row=1, col=2
    )

# ③ VIF
fig.add_trace(
    go.Bar(
        x=list(data['vif']['basic'].keys()),
        y=list(data['vif']['basic'].values()),
        name='기본'
    ),
    row=2, col=1
)

fig.add_trace(
    go.Bar(
        x=list(data['vif']['extended'].keys()),
        y=list(data['vif']['extended'].values()),
        name='확장'
    ),
    row=2, col=1
)

# ④ Scatter
scatter_df = pd.DataFrame({
    '유동인구': data['scatter_data']['population'],
    '매출': data['scatter_data']['sales'],
    '점포수': data['scatter_data']['store_count']
})

fig.add_trace(
    go.Scatter(
        x=scatter_df['유동인구'],
        y=scatter_df['매출'],
        mode='markers',
        marker=dict(size=6, opacity=0.6),
        name='매출'
    ),
    row=2, col=2
)

fig.update_layout(
    height=900,
    title_text='상권 분석 통합 대시보드',
    showlegend=True
)

fig.show()


In [ ]:
pip install streamlit

In [47]:
import streamlit as st
import json
import pandas as pd
import plotly.express as px

st.set_page_config(layout='wide')
st.title('📊 상권 분석 인터랙티브 리포트')

with open('analysis_results.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

# --- 상관계수 ---
st.subheader('1️⃣ 상관계수 분석')

corr_df = pd.DataFrame({
    '변수': data['correlation']['variables'],
    '상관계수': data['correlation']['r_values'],
    'p-value': data['correlation']['p_values']
})

st.plotly_chart(
    px.bar(corr_df, x='변수', y='상관계수', color='p-value'),
    use_container_width=True
)

# --- 회귀 결과 ---
st.subheader('2️⃣ 회귀 분석 결과')

col1, col2 = st.columns(2)

with col1:
    st.metric("기본 R²", round(data['regression_basic']['R2'], 3))
    st.metric("기본 Adj R²", round(data['regression_basic']['adj_R2'], 3))

with col2:
    st.metric("확장 R²", round(data['regression_extended']['R2'], 3))
    st.metric("확장 Adj R²", round(data['regression_extended']['adj_R2'], 3))

# --- Scatter ---
st.subheader('3️⃣ 유동인구 vs 매출')

scatter_df = pd.DataFrame({
    '유동인구': data['scatter_data']['population'],
    '매출': data['scatter_data']['sales'],
    '점포수': data['scatter_data']['store_count'],
})

fig = px.scatter(
    scatter_df,
    x='유동인구',
    y='매출',
    size='점포수',
    trendline='ols'
)

st.plotly_chart(fig, use_container_width=True)


2026-01-26 16:20:50.452 WARNING streamlit.runtime.scriptrunner_utils.script_run_context: Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2026-01-26 16:20:50.454 WARNING streamlit.runtime.scriptrunner_utils.script_run_context: Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2026-01-26 16:20:50.522 
  command:

    streamlit run c:\Users\Administrator\workspace\budongsan3_project\venv\Lib\site-packages\ipykernel_launcher.py [ARGUMENTS]
2026-01-26 16:20:50.523 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2026-01-26 16:20:50.524 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2026-01-26 16:20:50.526 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2026-01-26 16:20:50.527 Thread 'MainThread': missing ScriptRunContext! This 

DeltaGenerator()

In [48]:
x = np.array(scatter_df['유동인구'])
y = np.array(scatter_df['매출'])

# 단순 회귀
slope, intercept, r, p, se = stats.linregress(x, y)
y_pred = intercept + slope * x

# 신뢰구간
n = len(x)
t_val = stats.t.ppf(0.975, n - 2)
ci = t_val * se * np.sqrt(
    1/n + (x - np.mean(x))**2 / np.sum((x - np.mean(x))**2)
)

fig_reg = go.Figure()

fig_reg.add_trace(go.Scatter(
    x=x, y=y,
    mode='markers',
    name='관측값',
    opacity=0.5
))

fig_reg.add_trace(go.Scatter(
    x=x,
    y=y_pred,
    mode='lines',
    name='회귀선',
    line=dict(color='red')
))

fig_reg.add_trace(go.Scatter(
    x=np.concatenate([x, x[::-1]]),
    y=np.concatenate([y_pred + ci, (y_pred - ci)[::-1]]),
    fill='toself',
    fillcolor='rgba(255,0,0,0.2)',
    line=dict(color='rgba(255,255,255,0)'),
    name='95% 신뢰구간'
))

fig_reg.update_layout(
    title='유동인구 → 매출 회귀 분석',
    xaxis_title='유동인구',
    yaxis_title='매출'
)

fig_reg.show()
